In [ ]:
# Original data (will use for testing)

import pandas as pd

test_df = pd.read_csv("./data/curData.csv")
test_df = test_df.drop(columns=["issue_d"], axis=1)
test_df['issue_month'] = pd.to_datetime(test_df['issue_month'])
test_df["issue_month"] = test_df["issue_month"].dt.month
test_df = test_df.drop(columns=["Unnamed: 0", "Unnamed: 0.1"], axis=1)
test_df["purpose"] = test_df["purpose"].astype("category")
test_df["home_ownership"] = test_df["home_ownership"].astype("category")


feature_cols = ['loan_amnt', 'term', 'int_rate',
       'installment', 'purpose', 'emp_length', 'home_ownership', 'annual_inc',
       'dti', 'inq_last_6mths', 'delinq_2yrs', 'open_acc', 'pub_rec',
       'revol_bal', 'revol_util', 'total_acc', 'issue_month',
       'installment_to_income', 'fico_score', 'credit_age',
       'fed_funds_rate', 'unemployment_rate', 'cpi', 'real_gdp',
       'debt_service_ratio']

target = "loan_risk"

In [ ]:
# Training data

df = pd.read_csv("./data/smoteData.csv")

In [16]:
import optuna
import lightgbm as lgb
from sklearn.model_selection import train_test_split
from sklearn.metrics import roc_auc_score
from lightgbm.callback import early_stopping, log_evaluation

In [40]:
categorical = ["purpose", "home_ownership"]
for cat in categorical:
    df[cat] = df[cat].astype("category")

_, X_test, _, y_test = train_test_split(test_df[feature_cols], test_df[target], stratify=test_df[target], test_size=0.2, random_state=42)


In [41]:
X_train = df[feature_cols]
y_train = df[target]

In [ ]:
from lightgbm import LGBMClassifier
model = LGBMClassifier(device='gpu')
model.fit(X_train, y_train)

# Testing Cuda, works

[LightGBM] [Info] Number of positive: 1966639, number of negative: 1966639
[LightGBM] [Info] This is the GPU trainer!!
[LightGBM] [Debug] Dataset::GetMultiBinFromSparseFeatures: sparse rate 0.748540
[LightGBM] [Info] Total Bins 5397
[LightGBM] [Info] Number of data points in the train set: 3933278, number of used features: 25
[LightGBM] [Info] Using GPU Device: NVIDIA GeForce RTX 3060 Ti, Vendor: NVIDIA Corporation
[LightGBM] [Info] Compiling OpenCL Kernel with 256 bins...
[LightGBM] [Info] GPU programs have been built
[LightGBM] [Info] Size of histogram bin entry: 8
[LightGBM] [Info] 23 dense feature groups (90.03 MB) transferred to GPU in 0.055335 secs. 1 sparse feature groups
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.500000 -> initscore=0.000000
[LightGBM] [Debug] Trained a tree with leaves = 31 and depth = 11
[LightGBM] [Debug] Trained a tree with leaves = 31 and depth = 10
[LightGBM] [Debug] Trained a tree with leaves = 31 and depth = 9
[LightGBM] [Debug] Trained a tree wi

LGBMClassifier(device='gpu')

In [43]:
def objective(trial):
    param = {
        "objective": "binary",
        "metric": "auc",
        'boosting_type': 'gbdt',
        "device": "gpu",
        'verbosity': 2,
        'feature_pre_filter': False,
        'lambda_l1': trial.suggest_float('lambda_l1', 1e-8, 10.0, log=True),
        'lambda_l2': trial.suggest_float('lambda_l2', 1e-8, 10.0, log=True),
        'num_leaves': trial.suggest_int('num_leaves', 10, 256),
        'feature_fraction': trial.suggest_float('feature_fraction', 0.4, 1.0),
        'bagging_fraction': trial.suggest_float('bagging_fraction', 0.4, 1.0),
        'bagging_freq': trial.suggest_int('bagging_freq', 1, 7),
        'min_child_samples': trial.suggest_int('min_child_samples', 5, 100)
    }

    train_data = lgb.Dataset(X_train, label=y_train, categorical_feature=categorical)
    test_data = lgb.Dataset(X_test, label=y_test, categorical_feature=categorical)

    model = lgb.train(
        param,
        train_set=train_data,
        valid_sets=[test_data],
        num_boost_round=1000,
        callbacks=[
            lgb.early_stopping(stopping_rounds=20)
        ]
    )

    preds = model.predict(X_test)
    return roc_auc_score(y_test, preds)


In [44]:
study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=50)

[I 2025-07-21 03:25:26,430] A new study created in memory with name: no-name-497caa8d-72e7-4ee0-bbb0-fecffcc361d2


[LightGBM] [Info] Number of positive: 1966639, number of negative: 1966639
[LightGBM] [Info] This is the GPU trainer!!
[LightGBM] [Debug] Dataset::GetMultiBinFromSparseFeatures: sparse rate 0.748540
[LightGBM] [Info] Total Bins 5397
[LightGBM] [Info] Number of data points in the train set: 3933278, number of used features: 25
[LightGBM] [Info] Using GPU Device: NVIDIA GeForce RTX 3060 Ti, Vendor: NVIDIA Corporation
[LightGBM] [Info] Compiling OpenCL Kernel with 256 bins...
[LightGBM] [Info] GPU programs have been built
[LightGBM] [Info] Size of histogram bin entry: 8
[LightGBM] [Info] 23 dense feature groups (90.03 MB) transferred to GPU in 0.071769 secs. 1 sparse feature groups
[LightGBM] [Debug] Use subset for bagging
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.500000 -> initscore=0.000000
[LightGBM] [Debug] Re-bagging, using 2251425 data to train
[LightGBM] [Info] Size of histogram bin entry: 8
[LightGBM] [Info] 23 dense feature groups (51.53 MB) transferred to GPU in 0.039706

[I 2025-07-21 03:26:37,804] Trial 0 finished with value: 0.7721943131607908 and parameters: {'lambda_l1': 2.2930810780090925e-08, 'lambda_l2': 4.768746747429788e-07, 'num_leaves': 65, 'feature_fraction': 0.4625500337099094, 'bagging_fraction': 0.571539049872453, 'bagging_freq': 3, 'min_child_samples': 7}. Best is trial 0 with value: 0.7721943131607908.


[LightGBM] [Info] Number of positive: 1966639, number of negative: 1966639
[LightGBM] [Info] This is the GPU trainer!!
[LightGBM] [Debug] Dataset::GetMultiBinFromSparseFeatures: sparse rate 0.748540
[LightGBM] [Info] Total Bins 5397
[LightGBM] [Info] Number of data points in the train set: 3933278, number of used features: 25
[LightGBM] [Info] Using GPU Device: NVIDIA GeForce RTX 3060 Ti, Vendor: NVIDIA Corporation
[LightGBM] [Info] Compiling OpenCL Kernel with 256 bins...
[LightGBM] [Info] GPU programs have been built
[LightGBM] [Info] Size of histogram bin entry: 8
[LightGBM] [Info] 23 dense feature groups (90.03 MB) transferred to GPU in 0.070038 secs. 1 sparse feature groups
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.500000 -> initscore=0.000000
[LightGBM] [Debug] Re-bagging, using 2394747 data to train
[LightGBM] [Debug] Trained a tree with leaves = 220 and depth = 19
Training until validation scores don't improve for 20 rounds
[LightGBM] [Debug] Re-bagging, using 2391999 d

[I 2025-07-21 03:29:40,562] Trial 1 finished with value: 0.8753113091957145 and parameters: {'lambda_l1': 0.5103243488753683, 'lambda_l2': 4.1263846041307847e-08, 'num_leaves': 220, 'feature_fraction': 0.7560888653686089, 'bagging_fraction': 0.6080688770358733, 'bagging_freq': 1, 'min_child_samples': 84}. Best is trial 1 with value: 0.8753113091957145.


...

[I 2025-07-21 05:40:51,086] Trial 47 finished with value: 0.8832823941576209 and parameters: {'lambda_l1': 2.1573308630340382e-05, 'lambda_l2': 0.00802682896158706, 'num_leaves': 220, 'feature_fraction': 0.8143539084914817, 'bagging_fraction': 0.5236337969346864, 'bagging_freq': 4, 'min_child_samples': 19}. Best is trial 46 with value: 0.8944978009086826.


[LightGBM] [Info] Number of positive: 1966639, number of negative: 1966639
[LightGBM] [Info] This is the GPU trainer!!
[LightGBM] [Debug] Dataset::GetMultiBinFromSparseFeatures: sparse rate 0.748540
[LightGBM] [Info] Total Bins 5397
[LightGBM] [Info] Number of data points in the train set: 3933278, number of used features: 25
[LightGBM] [Info] Using GPU Device: NVIDIA GeForce RTX 3060 Ti, Vendor: NVIDIA Corporation
[LightGBM] [Info] Compiling OpenCL Kernel with 256 bins...
[LightGBM] [Info] GPU programs have been built
[LightGBM] [Info] Size of histogram bin entry: 8
[LightGBM] [Info] 23 dense feature groups (90.03 MB) transferred to GPU in 0.069489 secs. 1 sparse feature groups
[LightGBM] [Debug] Use subset for bagging
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.500000 -> initscore=0.000000
[LightGBM] [Debug] Re-bagging, using 1938360 data to train
[LightGBM] [Info] Size of histogram bin entry: 8
[LightGBM] [Info] 23 dense feature groups (44.37 MB) transferred to GPU in 0.033679

[I 2025-07-21 05:43:54,827] Trial 48 finished with value: 0.8648712991534486 and parameters: {'lambda_l1': 0.00028356725582491483, 'lambda_l2': 0.0004888387171410927, 'num_leaves': 189, 'feature_fraction': 0.9225521278545122, 'bagging_fraction': 0.49207608782405027, 'bagging_freq': 3, 'min_child_samples': 37}. Best is trial 46 with value: 0.8944978009086826.


[LightGBM] [Info] Number of positive: 1966639, number of negative: 1966639
[LightGBM] [Info] This is the GPU trainer!!
[LightGBM] [Debug] Dataset::GetMultiBinFromSparseFeatures: sparse rate 0.748540
[LightGBM] [Info] Total Bins 5397
[LightGBM] [Info] Number of data points in the train set: 3933278, number of used features: 25
[LightGBM] [Info] Using GPU Device: NVIDIA GeForce RTX 3060 Ti, Vendor: NVIDIA Corporation
[LightGBM] [Info] Compiling OpenCL Kernel with 256 bins...
[LightGBM] [Info] GPU programs have been built
[LightGBM] [Info] Size of histogram bin entry: 8
[LightGBM] [Info] 23 dense feature groups (90.03 MB) transferred to GPU in 0.069862 secs. 1 sparse feature groups
[LightGBM] [Debug] Use subset for bagging
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.500000 -> initscore=0.000000
[LightGBM] [Debug] Re-bagging, using 1771490 data to train
[LightGBM] [Info] Size of histogram bin entry: 8
[LightGBM] [Info] 23 dense feature groups (40.55 MB) transferred to GPU in 0.031520

[I 2025-07-21 05:47:17,988] Trial 49 finished with value: 0.8902754543034099 and parameters: {'lambda_l1': 4.302709663938219e-06, 'lambda_l2': 9.915061974998078e-05, 'num_leaves': 248, 'feature_fraction': 0.7876012369779112, 'bagging_fraction': 0.44967139171763393, 'bagging_freq': 4, 'min_child_samples': 27}. Best is trial 46 with value: 0.8944978009086826.


In [45]:
study.best_params

{'lambda_l1': 0.000306009500542766,
 'lambda_l2': 8.279259632222018e-05,
 'num_leaves': 248,
 'feature_fraction': 0.816224984482257,
 'bagging_fraction': 0.5222257216310624,
 'bagging_freq': 4,
 'min_child_samples': 18}

In [46]:
best_params = study.best_params
best_model = lgb.LGBMClassifier(
    **best_params,
    device="gpu",
    n_estimators=1000,
    boosting_type="gbdt",
    objective="binary",
    random_state=42
)

In [47]:
best_model.fit(df[feature_cols], df[target])

[LightGBM] [Warning] feature_fraction is set=0.816224984482257, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.816224984482257
[LightGBM] [Warning] lambda_l1 is set=0.000306009500542766, reg_alpha=0.0 will be ignored. Current value: lambda_l1=0.000306009500542766
[LightGBM] [Warning] lambda_l2 is set=8.279259632222018e-05, reg_lambda=0.0 will be ignored. Current value: lambda_l2=8.279259632222018e-05
[LightGBM] [Warning] bagging_fraction is set=0.5222257216310624, subsample=1.0 will be ignored. Current value: bagging_fraction=0.5222257216310624
[LightGBM] [Warning] bagging_freq is set=4, subsample_freq=0 will be ignored. Current value: bagging_freq=4
[LightGBM] [Warning] feature_fraction is set=0.816224984482257, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.816224984482257
[LightGBM] [Warning] lambda_l1 is set=0.000306009500542766, reg_alpha=0.0 will be ignored. Current value: lambda_l1=0.000306009500542766
[LightGBM] [Warning] lambda

LGBMClassifier(bagging_fraction=0.5222257216310624, bagging_freq=4,
               device='gpu', feature_fraction=0.816224984482257,
               lambda_l1=0.000306009500542766, lambda_l2=8.279259632222018e-05,
               min_child_samples=18, n_estimators=1000, num_leaves=248,
               objective='binary', random_state=42)

In [49]:
from sklearn.metrics import roc_auc_score

y_pred = best_model.predict(df[feature_cols])
print("Original AUC:", roc_auc_score(df[target], y_pred))

[LightGBM] [Warning] feature_fraction is set=0.816224984482257, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.816224984482257
[LightGBM] [Warning] lambda_l1 is set=0.000306009500542766, reg_alpha=0.0 will be ignored. Current value: lambda_l1=0.000306009500542766
[LightGBM] [Warning] lambda_l2 is set=8.279259632222018e-05, reg_lambda=0.0 will be ignored. Current value: lambda_l2=8.279259632222018e-05
[LightGBM] [Warning] bagging_fraction is set=0.5222257216310624, subsample=1.0 will be ignored. Current value: bagging_fraction=0.5222257216310624
[LightGBM] [Warning] bagging_freq is set=4, subsample_freq=0 will be ignored. Current value: bagging_freq=4
Original AUC: 0.9342334815896562


In [48]:
from sklearn.metrics import roc_auc_score

y_pred = best_model.predict(test_df[feature_cols])
print("Original AUC:", roc_auc_score(test_df[target], y_pred))

[LightGBM] [Warning] feature_fraction is set=0.816224984482257, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.816224984482257
[LightGBM] [Warning] lambda_l1 is set=0.000306009500542766, reg_alpha=0.0 will be ignored. Current value: lambda_l1=0.000306009500542766
[LightGBM] [Warning] lambda_l2 is set=8.279259632222018e-05, reg_lambda=0.0 will be ignored. Current value: lambda_l2=8.279259632222018e-05
[LightGBM] [Warning] bagging_fraction is set=0.5222257216310624, subsample=1.0 will be ignored. Current value: bagging_fraction=0.5222257216310624
[LightGBM] [Warning] bagging_freq is set=4, subsample_freq=0 will be ignored. Current value: bagging_freq=4
Original AUC: 0.5606651237710478


In [56]:
# No SMOTE, just using light gbm imbalance
X_train, X_test, y_train, y_test = train_test_split(test_df[feature_cols], test_df[target], stratify=test_df[target], test_size=0.2, random_state=42)

params = {'lambda_l1': 0.000306009500542766,
 'lambda_l2': 8.279259632222018e-05,
 'num_leaves': 248,
 'feature_fraction': 0.816224984482257,
 'bagging_fraction': 0.5222257216310624,
 'bagging_freq': 4,
 'min_child_samples': 18}

test_model = lgb.LGBMClassifier(
    **params,
    boosting_type="gbdt",
    objective="binary",
    random_state=42,
    is_unbalance=True
)

test_model.fit(X_train, y_train, eval_metric="auc")

[LightGBM] [Warning] feature_fraction is set=0.816224984482257, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.816224984482257
[LightGBM] [Warning] lambda_l1 is set=0.000306009500542766, reg_alpha=0.0 will be ignored. Current value: lambda_l1=0.000306009500542766
[LightGBM] [Warning] lambda_l2 is set=8.279259632222018e-05, reg_lambda=0.0 will be ignored. Current value: lambda_l2=8.279259632222018e-05
[LightGBM] [Warning] bagging_fraction is set=0.5222257216310624, subsample=1.0 will be ignored. Current value: bagging_fraction=0.5222257216310624
[LightGBM] [Warning] bagging_freq is set=4, subsample_freq=0 will be ignored. Current value: bagging_freq=4
[LightGBM] [Warning] feature_fraction is set=0.816224984482257, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.816224984482257
[LightGBM] [Warning] lambda_l1 is set=0.000306009500542766, reg_alpha=0.0 will be ignored. Current value: lambda_l1=0.000306009500542766
[LightGBM] [Warning] lambda

LGBMClassifier(bagging_fraction=0.5222257216310624, bagging_freq=4,
               feature_fraction=0.816224984482257, is_unbalance=True,
               lambda_l1=0.000306009500542766, lambda_l2=8.279259632222018e-05,
               min_child_samples=18, num_leaves=248, objective='binary',
               random_state=42)

In [57]:
from sklearn.metrics import roc_auc_score

y_pred = test_model.predict(X_test)
print("Original AUC:", roc_auc_score(y_test, y_pred))

[LightGBM] [Warning] feature_fraction is set=0.816224984482257, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.816224984482257
[LightGBM] [Warning] lambda_l1 is set=0.000306009500542766, reg_alpha=0.0 will be ignored. Current value: lambda_l1=0.000306009500542766
[LightGBM] [Warning] lambda_l2 is set=8.279259632222018e-05, reg_lambda=0.0 will be ignored. Current value: lambda_l2=8.279259632222018e-05
[LightGBM] [Warning] bagging_fraction is set=0.5222257216310624, subsample=1.0 will be ignored. Current value: bagging_fraction=0.5222257216310624
[LightGBM] [Warning] bagging_freq is set=4, subsample_freq=0 will be ignored. Current value: bagging_freq=4
Original AUC: 0.687766074013344
